<h1><center> NASA Airathon - NO2 Track </center></h1>

### <center> Extract GFS data corresponding to training labels </center>

<div style="text-align: center"> 
    Dr. Sukanta Basu <br/> Associate Professor <br/> Delft University of Technology, The Netherlands <br/> Email: s.basu@tudelft.nl<br/> https://sites.google.com/view/sukantabasu/
</div>

#### Log

Last updated: 4th April, 2022

Midnight to Midnight:
LAX: 8Z     - 32Z (I consider forecast hours: 6:3:30)
DEL: 18:30Z - 42:30Z (I consider forecast hours: 18:3:42)
TAI: 16Z    - 40Z (I consider forecast hours: 15:3:39)
Note: when 12 am starts at LAX, it is 8 pm at Taipei. 

#### User instructions

Before running this notebook, please extract the GFS files in individual sub-directories. See README_airathon.md for details.  

#### Load packages

In [1]:
import numpy as np
from matplotlib import pyplot as plt
import pandas as pd
from pathlib import Path
import netCDF4

#### Directories

In [2]:
ROOT_DIR    = '../../'

#Please update this directory depending on the location of the extracted GFS data
GFS_DIR     = '../../data/airathon/raw/GFS/'

#Location of processed datasets
EXTDATA_DIR = ROOT_DIR + 'data/airathon/processed/'

#### Load combo data

In [3]:
df_OBS    = pd.read_csv(EXTDATA_DIR + 'train/STN/' + 'trainOBS.csv') #Contains: datetime, ID, latitude, longitude, NO2
nSamples  = np.size(df_OBS['NO2'])

In [4]:
NO2  = df_OBS['NO2']
LONx = df_OBS['longitude']
LATx = df_OBS['latitude']

YR = (pd.to_datetime(df_OBS['datetime'])).dt.year
MO = (pd.to_datetime(df_OBS['datetime'])).dt.month
DY = (pd.to_datetime(df_OBS['datetime'])).dt.day
JD = (pd.to_datetime(df_OBS['datetime'])).dt.dayofyear
WD = (pd.to_datetime(df_OBS['datetime'])).dt.weekday
HR = 0 #Only consider 0 UTC cycle

#### Compute nearest point

In [5]:
def nearestGridFAST(LAT,LON,LATx,LONx):
    
    dLAT = np.abs(LAT - LATx)
    dLON = np.abs(LON - LONx)
    
    dTOT = dLAT + dLON #taxi-cab distance
    
    #https://stackoverflow.com/questions/3230067/numpy-minimum-in-row-column-format
    r_min, c_min = np.unravel_index(dTOT.argmin(), dTOT.shape)
    
    return r_min, c_min

#### Extract GFS

In [6]:
GFSdata = np.zeros((nSamples,13*9)) #13 variables (PBLH, M10, M100, alpha, sinX100, cosX100, 
                                    #beta, SHFX, VENT, RH, T2, T100-T2, Rig); 
                                    #24 h = 9 x 3-hourly samples spanning 0 h to 0 h

for n in range(nSamples):
    
    if (LONx[n] > 120) & (LONx[n] < 122):
        strCITY = 'TAI/'
        fcstHRini = 15
        fcstHRfin = 39+1
    elif (LONx[n] > 76) & (LONx[n] < 78):
        strCITY = 'DEL/'
        fcstHRini = 18
        fcstHRfin = 42+1
    elif (LONx[n] > -119) & (LONx[n] < -116):
        strCITY = 'LAX/'
        fcstHRini = 6
        fcstHRfin = 30+1        
    else:
        strCITY = 'XXX/'
    
    cnt = 0
    for fcstHR in np.arange(fcstHRini,fcstHRfin,3): 
        
        strFILE = 'gfs.0p25.' + str(YR[n]) + str(MO[n]).zfill(2) + str(DY[n]).zfill(2) + str(HR).zfill(2) + '.f' + str(fcstHR).zfill(3) + '.grib2.nc'
        
        #-----------------
        strVAR = 'PBLH/'
        filePBLH = Path(GFS_DIR + strCITY + strVAR + strFILE)
        dataPBLH = netCDF4.Dataset(filePBLH,'r')
        
        LAT  = dataPBLH.variables['lat'][:]
        LON  = dataPBLH.variables['lon'][:]
        if (strCITY == 'LAX/'): 
            LON = LON - 360 #GFS outputs data as 240 E instead of -120 W
        LON2d, LAT2d = np.meshgrid(LON,LAT)
            
        PBLH         = np.squeeze(dataPBLH.variables['HPBL_L1'][:])  
        
        r_min, c_min = nearestGridFAST(LAT2d,LON2d,LATx[n],LONx[n])
        
        PBLHi = PBLH[r_min][c_min]
        GFSdata[n,cnt] = PBLHi
        cnt = cnt + 1
        #-----------------
        
        #-----------------
        strVAR    = 'U/'
        fileU     = Path(GFS_DIR + strCITY + strVAR + strFILE)
        dataU     = netCDF4.Dataset(fileU,'r')
        U         = np.squeeze(dataU.variables['U_GRD_L103'][:])     
        U100      = np.squeeze(U[0,:,:])
        U10       = np.squeeze(U[1,:,:])
        U100i     = U100[r_min][c_min]
        U10i      = U10[r_min][c_min]
        #-----------------
        
        #-----------------
        strVAR    = 'V/'
        fileV     = Path(GFS_DIR + strCITY + strVAR + strFILE)
        dataV     = netCDF4.Dataset(fileV,'r')
        V         = np.squeeze(dataV.variables['V_GRD_L103'][:])     
        V100      = np.squeeze(V[0,:,:])
        V10       = np.squeeze(V[1,:,:])
        V100i     = V100[r_min][c_min]
        V10i      = V10[r_min][c_min]
        #-----------------

        #-----------------
        M10i      = np.sqrt(U10i**2  + V10i**2)
        M100i     = np.sqrt(U100i**2 + V100i**2)
        alpha     = np.log(M100i/M10i)/np.log(10)
        
        RtoD      = 180/np.pi
        X10i      = np.arctan2(-U10i,-V10i)*RtoD
        if X10i < 0:
            X10i = X10i + 360
        X100i     = np.arctan2(-U100i,-V100i)*RtoD
        if X100i < 0:
            X100i = X100i + 360
        sinX100i  = np.sin(X100i/RtoD)
        cosX100i  = np.cos(X100i/RtoD)
        beta      = np.abs(X100i-X10i)
        if beta > 180:
            beta = 360 - beta
        
        GFSdata[n,cnt] = M10i
        cnt = cnt + 1
        
        GFSdata[n,cnt] = M100i
        cnt = cnt + 1
        
        GFSdata[n,cnt] = alpha 
        cnt = cnt + 1
        
        GFSdata[n,cnt] = sinX100i 
        cnt = cnt + 1

        GFSdata[n,cnt] = cosX100i 
        cnt = cnt + 1

        GFSdata[n,cnt] = beta 
        cnt = cnt + 1
        #-----------------

        #-----------------
        strVAR    = 'SHFX/'
        fileSHFX  = Path(GFS_DIR + strCITY + strVAR + strFILE)
        dataSHFX  = netCDF4.Dataset(fileSHFX,'r')
        SHFX      = np.squeeze(dataSHFX.variables['SHTFL_L1_Avg_1'][:])     
        SHFXi     = SHFX[r_min][c_min]

        GFSdata[n,cnt] = SHFXi
        cnt = cnt + 1        
        #-----------------
        
        #-----------------
        strVAR    = 'VENT/'
        fileVENT  = Path(GFS_DIR + strCITY + strVAR + strFILE)
        dataVENT  = netCDF4.Dataset(fileVENT,'r')
        VENT      = np.squeeze(dataVENT.variables['VRATE_L220'][:])     
        VENTi     = VENT[r_min][c_min]

        GFSdata[n,cnt] = VENTi
        cnt = cnt + 1        
        #-----------------
        
        #-----------------
        strVAR    = 'RH/'
        fileRH    = Path(GFS_DIR + strCITY + strVAR + strFILE)
        dataRH    = netCDF4.Dataset(fileRH,'r')
        RH        = np.squeeze(dataRH.variables['R_H_L103'][:])     
        RHi       = RH[r_min][c_min]

        GFSdata[n,cnt] = RHi
        cnt = cnt + 1        
        #-----------------
        
        #-----------------
        strVAR    = 'T2/'
        fileT2    = Path(GFS_DIR + strCITY + strVAR + strFILE)
        dataT2    = netCDF4.Dataset(fileT2,'r')
        T2        = np.squeeze(dataT2.variables['TMP_L103'][:])     
        T2i       = T2[r_min][c_min]

        GFSdata[n,cnt] = T2i
        cnt = cnt + 1        
        #-----------------

        #-----------------
        strVAR    = 'T100/'
        fileT100  = Path(GFS_DIR + strCITY + strVAR + strFILE)
        dataT100  = netCDF4.Dataset(fileT100,'r')
        T100      = np.squeeze(dataT100.variables['TMP_L103'][:])     
        T100i     = T100[r_min][c_min]

        GFSdata[n,cnt] = T100i - T2i
        cnt = cnt + 1        
        #-----------------

        #-----------------
        GFSdata[n,cnt] = (T100i - T2i)/(M100i - M10i)**2
        cnt = cnt + 1                
        #-----------------
        
        print((n,nSamples))

(0, 36131)
(0, 36131)
(0, 36131)
(0, 36131)
(0, 36131)
(0, 36131)
(0, 36131)
(0, 36131)
(0, 36131)
(1, 36131)
(1, 36131)
(1, 36131)
(1, 36131)
(1, 36131)
(1, 36131)
(1, 36131)
(1, 36131)
(1, 36131)
(2, 36131)
(2, 36131)
(2, 36131)
(2, 36131)
(2, 36131)
(2, 36131)
(2, 36131)
(2, 36131)
(2, 36131)
(3, 36131)
(3, 36131)
(3, 36131)
(3, 36131)
(3, 36131)
(3, 36131)
(3, 36131)
(3, 36131)
(3, 36131)
(4, 36131)
(4, 36131)
(4, 36131)
(4, 36131)
(4, 36131)
(4, 36131)
(4, 36131)
(4, 36131)
(4, 36131)
(5, 36131)
(5, 36131)
(5, 36131)
(5, 36131)
(5, 36131)
(5, 36131)
(5, 36131)
(5, 36131)
(5, 36131)
(6, 36131)
(6, 36131)
(6, 36131)
(6, 36131)
(6, 36131)
(6, 36131)
(6, 36131)
(6, 36131)
(6, 36131)
(7, 36131)
(7, 36131)
(7, 36131)
(7, 36131)
(7, 36131)
(7, 36131)
(7, 36131)
(7, 36131)
(7, 36131)
(8, 36131)
(8, 36131)
(8, 36131)
(8, 36131)
(8, 36131)
(8, 36131)
(8, 36131)
(8, 36131)
(8, 36131)
(9, 36131)
(9, 36131)
(9, 36131)
(9, 36131)
(9, 36131)
(9, 36131)
(9, 36131)
(9, 36131)
(9, 36131)
(10, 36131

(81, 36131)
(81, 36131)
(81, 36131)
(81, 36131)
(81, 36131)
(81, 36131)
(82, 36131)
(82, 36131)
(82, 36131)
(82, 36131)
(82, 36131)
(82, 36131)
(82, 36131)
(82, 36131)
(82, 36131)
(83, 36131)
(83, 36131)
(83, 36131)
(83, 36131)
(83, 36131)
(83, 36131)
(83, 36131)
(83, 36131)
(83, 36131)
(84, 36131)
(84, 36131)
(84, 36131)
(84, 36131)
(84, 36131)
(84, 36131)
(84, 36131)
(84, 36131)
(84, 36131)
(85, 36131)
(85, 36131)
(85, 36131)
(85, 36131)
(85, 36131)
(85, 36131)
(85, 36131)
(85, 36131)
(85, 36131)
(86, 36131)
(86, 36131)
(86, 36131)
(86, 36131)
(86, 36131)
(86, 36131)
(86, 36131)
(86, 36131)
(86, 36131)
(87, 36131)
(87, 36131)
(87, 36131)
(87, 36131)
(87, 36131)
(87, 36131)
(87, 36131)
(87, 36131)
(87, 36131)
(88, 36131)
(88, 36131)
(88, 36131)
(88, 36131)
(88, 36131)
(88, 36131)
(88, 36131)
(88, 36131)
(88, 36131)
(89, 36131)
(89, 36131)
(89, 36131)
(89, 36131)
(89, 36131)
(89, 36131)
(89, 36131)
(89, 36131)
(89, 36131)
(90, 36131)
(90, 36131)
(90, 36131)
(90, 36131)
(90, 36131)
(90,

(156, 36131)
(156, 36131)
(156, 36131)
(157, 36131)
(157, 36131)
(157, 36131)
(157, 36131)
(157, 36131)
(157, 36131)
(157, 36131)
(157, 36131)
(157, 36131)
(158, 36131)
(158, 36131)
(158, 36131)
(158, 36131)
(158, 36131)
(158, 36131)
(158, 36131)
(158, 36131)
(158, 36131)
(159, 36131)
(159, 36131)
(159, 36131)
(159, 36131)
(159, 36131)
(159, 36131)
(159, 36131)
(159, 36131)
(159, 36131)
(160, 36131)
(160, 36131)
(160, 36131)
(160, 36131)
(160, 36131)
(160, 36131)
(160, 36131)
(160, 36131)
(160, 36131)
(161, 36131)
(161, 36131)
(161, 36131)
(161, 36131)
(161, 36131)
(161, 36131)
(161, 36131)
(161, 36131)
(161, 36131)
(162, 36131)
(162, 36131)
(162, 36131)
(162, 36131)
(162, 36131)
(162, 36131)
(162, 36131)
(162, 36131)
(162, 36131)
(163, 36131)
(163, 36131)
(163, 36131)
(163, 36131)
(163, 36131)
(163, 36131)
(163, 36131)
(163, 36131)
(163, 36131)
(164, 36131)
(164, 36131)
(164, 36131)
(164, 36131)
(164, 36131)
(164, 36131)
(164, 36131)
(164, 36131)
(164, 36131)
(165, 36131)
(165, 36131)

(228, 36131)
(228, 36131)
(228, 36131)
(228, 36131)
(228, 36131)
(228, 36131)
(228, 36131)
(228, 36131)
(228, 36131)
(229, 36131)
(229, 36131)
(229, 36131)
(229, 36131)
(229, 36131)
(229, 36131)
(229, 36131)
(229, 36131)
(229, 36131)
(230, 36131)
(230, 36131)
(230, 36131)
(230, 36131)
(230, 36131)
(230, 36131)
(230, 36131)
(230, 36131)
(230, 36131)
(231, 36131)
(231, 36131)
(231, 36131)
(231, 36131)
(231, 36131)
(231, 36131)
(231, 36131)
(231, 36131)
(231, 36131)
(232, 36131)
(232, 36131)
(232, 36131)
(232, 36131)
(232, 36131)
(232, 36131)
(232, 36131)
(232, 36131)
(232, 36131)
(233, 36131)
(233, 36131)
(233, 36131)
(233, 36131)
(233, 36131)
(233, 36131)
(233, 36131)
(233, 36131)
(233, 36131)
(234, 36131)
(234, 36131)
(234, 36131)
(234, 36131)
(234, 36131)
(234, 36131)
(234, 36131)
(234, 36131)
(234, 36131)
(235, 36131)
(235, 36131)
(235, 36131)
(235, 36131)
(235, 36131)
(235, 36131)
(235, 36131)
(235, 36131)
(235, 36131)
(236, 36131)
(236, 36131)
(236, 36131)
(236, 36131)
(236, 36131)

(301, 36131)
(302, 36131)
(302, 36131)
(302, 36131)
(302, 36131)
(302, 36131)
(302, 36131)
(302, 36131)
(302, 36131)
(302, 36131)
(303, 36131)
(303, 36131)
(303, 36131)
(303, 36131)
(303, 36131)
(303, 36131)
(303, 36131)
(303, 36131)
(303, 36131)
(304, 36131)
(304, 36131)
(304, 36131)
(304, 36131)
(304, 36131)
(304, 36131)
(304, 36131)
(304, 36131)
(304, 36131)
(305, 36131)
(305, 36131)
(305, 36131)
(305, 36131)
(305, 36131)
(305, 36131)
(305, 36131)
(305, 36131)
(305, 36131)
(306, 36131)
(306, 36131)
(306, 36131)
(306, 36131)
(306, 36131)
(306, 36131)
(306, 36131)
(306, 36131)
(306, 36131)
(307, 36131)
(307, 36131)
(307, 36131)
(307, 36131)
(307, 36131)
(307, 36131)
(307, 36131)
(307, 36131)
(307, 36131)
(308, 36131)
(308, 36131)
(308, 36131)
(308, 36131)
(308, 36131)
(308, 36131)
(308, 36131)
(308, 36131)
(308, 36131)
(309, 36131)
(309, 36131)
(309, 36131)
(309, 36131)
(309, 36131)
(309, 36131)
(309, 36131)
(309, 36131)
(309, 36131)
(310, 36131)
(310, 36131)
(310, 36131)
(310, 36131)

...

(35861, 36131)
(35861, 36131)
(35861, 36131)
(35861, 36131)
(35861, 36131)
(35862, 36131)
(35862, 36131)
(35862, 36131)
(35862, 36131)
(35862, 36131)
(35862, 36131)
(35862, 36131)
(35862, 36131)
(35862, 36131)
(35863, 36131)
(35863, 36131)
(35863, 36131)
(35863, 36131)
(35863, 36131)
(35863, 36131)
(35863, 36131)
(35863, 36131)
(35863, 36131)
(35864, 36131)
(35864, 36131)
(35864, 36131)
(35864, 36131)
(35864, 36131)
(35864, 36131)
(35864, 36131)
(35864, 36131)
(35864, 36131)
(35865, 36131)
(35865, 36131)
(35865, 36131)
(35865, 36131)
(35865, 36131)
(35865, 36131)
(35865, 36131)
(35865, 36131)
(35865, 36131)
(35866, 36131)
(35866, 36131)
(35866, 36131)
(35866, 36131)
(35866, 36131)
(35866, 36131)
(35866, 36131)
(35866, 36131)
(35866, 36131)
(35867, 36131)
(35867, 36131)
(35867, 36131)
(35867, 36131)
(35867, 36131)
(35867, 36131)
(35867, 36131)
(35867, 36131)
(35867, 36131)
(35868, 36131)
(35868, 36131)
(35868, 36131)
(35868, 36131)
(35868, 36131)
(35868, 36131)
(35868, 36131)
(35868, 36

(35924, 36131)
(35924, 36131)
(35924, 36131)
(35924, 36131)
(35924, 36131)
(35924, 36131)
(35924, 36131)
(35924, 36131)
(35925, 36131)
(35925, 36131)
(35925, 36131)
(35925, 36131)
(35925, 36131)
(35925, 36131)
(35925, 36131)
(35925, 36131)
(35925, 36131)
(35926, 36131)
(35926, 36131)
(35926, 36131)
(35926, 36131)
(35926, 36131)
(35926, 36131)
(35926, 36131)
(35926, 36131)
(35926, 36131)
(35927, 36131)
(35927, 36131)
(35927, 36131)
(35927, 36131)
(35927, 36131)
(35927, 36131)
(35927, 36131)
(35927, 36131)
(35927, 36131)
(35928, 36131)
(35928, 36131)
(35928, 36131)
(35928, 36131)
(35928, 36131)
(35928, 36131)
(35928, 36131)
(35928, 36131)
(35928, 36131)
(35929, 36131)
(35929, 36131)
(35929, 36131)
(35929, 36131)
(35929, 36131)
(35929, 36131)
(35929, 36131)
(35929, 36131)
(35929, 36131)
(35930, 36131)
(35930, 36131)
(35930, 36131)
(35930, 36131)
(35930, 36131)
(35930, 36131)
(35930, 36131)
(35930, 36131)
(35930, 36131)
(35931, 36131)
(35931, 36131)
(35931, 36131)
(35931, 36131)
(35931, 36

(35985, 36131)
(35985, 36131)
(35985, 36131)
(35985, 36131)
(35986, 36131)
(35986, 36131)
(35986, 36131)
(35986, 36131)
(35986, 36131)
(35986, 36131)
(35986, 36131)
(35986, 36131)
(35986, 36131)
(35987, 36131)
(35987, 36131)
(35987, 36131)
(35987, 36131)
(35987, 36131)
(35987, 36131)
(35987, 36131)
(35987, 36131)
(35987, 36131)
(35988, 36131)
(35988, 36131)
(35988, 36131)
(35988, 36131)
(35988, 36131)
(35988, 36131)
(35988, 36131)
(35988, 36131)
(35988, 36131)
(35989, 36131)
(35989, 36131)
(35989, 36131)
(35989, 36131)
(35989, 36131)
(35989, 36131)
(35989, 36131)
(35989, 36131)
(35989, 36131)
(35990, 36131)
(35990, 36131)
(35990, 36131)
(35990, 36131)
(35990, 36131)
(35990, 36131)
(35990, 36131)
(35990, 36131)
(35990, 36131)
(35991, 36131)
(35991, 36131)
(35991, 36131)
(35991, 36131)
(35991, 36131)
(35991, 36131)
(35991, 36131)
(35991, 36131)
(35991, 36131)
(35992, 36131)
(35992, 36131)
(35992, 36131)
(35992, 36131)
(35992, 36131)
(35992, 36131)
(35992, 36131)
(35992, 36131)
(35992, 36

(36048, 36131)
(36048, 36131)
(36048, 36131)
(36048, 36131)
(36048, 36131)
(36049, 36131)
(36049, 36131)
(36049, 36131)
(36049, 36131)
(36049, 36131)
(36049, 36131)
(36049, 36131)
(36049, 36131)
(36049, 36131)
(36050, 36131)
(36050, 36131)
(36050, 36131)
(36050, 36131)
(36050, 36131)
(36050, 36131)
(36050, 36131)
(36050, 36131)
(36050, 36131)
(36051, 36131)
(36051, 36131)
(36051, 36131)
(36051, 36131)
(36051, 36131)
(36051, 36131)
(36051, 36131)
(36051, 36131)
(36051, 36131)
(36052, 36131)
(36052, 36131)
(36052, 36131)
(36052, 36131)
(36052, 36131)
(36052, 36131)
(36052, 36131)
(36052, 36131)
(36052, 36131)
(36053, 36131)
(36053, 36131)
(36053, 36131)
(36053, 36131)
(36053, 36131)
(36053, 36131)
(36053, 36131)
(36053, 36131)
(36053, 36131)
(36054, 36131)
(36054, 36131)
(36054, 36131)
(36054, 36131)
(36054, 36131)
(36054, 36131)
(36054, 36131)
(36054, 36131)
(36054, 36131)
(36055, 36131)
(36055, 36131)
(36055, 36131)
(36055, 36131)
(36055, 36131)
(36055, 36131)
(36055, 36131)
(36055, 36

(36113, 36131)
(36114, 36131)
(36114, 36131)
(36114, 36131)
(36114, 36131)
(36114, 36131)
(36114, 36131)
(36114, 36131)
(36114, 36131)
(36114, 36131)
(36115, 36131)
(36115, 36131)
(36115, 36131)
(36115, 36131)
(36115, 36131)
(36115, 36131)
(36115, 36131)
(36115, 36131)
(36115, 36131)
(36116, 36131)
(36116, 36131)
(36116, 36131)
(36116, 36131)
(36116, 36131)
(36116, 36131)
(36116, 36131)
(36116, 36131)
(36116, 36131)
(36117, 36131)
(36117, 36131)
(36117, 36131)
(36117, 36131)
(36117, 36131)
(36117, 36131)
(36117, 36131)
(36117, 36131)
(36117, 36131)
(36118, 36131)
(36118, 36131)
(36118, 36131)
(36118, 36131)
(36118, 36131)
(36118, 36131)
(36118, 36131)
(36118, 36131)
(36118, 36131)
(36119, 36131)
(36119, 36131)
(36119, 36131)
(36119, 36131)
(36119, 36131)
(36119, 36131)
(36119, 36131)
(36119, 36131)
(36119, 36131)
(36120, 36131)
(36120, 36131)
(36120, 36131)
(36120, 36131)
(36120, 36131)
(36120, 36131)
(36120, 36131)
(36120, 36131)
(36120, 36131)
(36121, 36131)
(36121, 36131)
(36121, 36

In [7]:
df_new = pd.DataFrame(data=GFSdata)
df_new.columns = ['PBLH_0' ,'M10_0' ,'M100_0' ,'alpha_0', 'sinX100_0', 'cosX100_0', 
                  'beta_0', 'SHFX_0', 'VENT_0', 'RH_0', 'T2_0', 'dT_0', 'Rig_0',
                  'PBLH_3' ,'M10_3' ,'M100_3' ,'alpha_3', 'sinX100_3', 'cosX100_3', 
                  'beta_3', 'SHFX_3', 'VENT_3', 'RH_3', 'T2_3', 'dT_3', 'Rig_3',
                  'PBLH_6' ,'M10_6' ,'M100_6' ,'alpha_6', 'sinX100_6', 'cosX100_6', 
                  'beta_6', 'SHFX_6', 'VENT_6', 'RH_6', 'T2_6', 'dT_6', 'Rig_6',
                  'PBLH_9' ,'M10_9' ,'M100_9' ,'alpha_9', 'sinX100_9', 'cosX100_9', 
                  'beta_9', 'SHFX_9', 'VENT_9', 'RH_9', 'T2_9', 'dT_9', 'Rig_9',
                  'PBLH_12','M10_12','M100_12','alpha_12','sinX100_12','cosX100_12',
                  'beta_12','SHFX_12','VENT_12','RH_12','T2_12','dT_12','Rig_12',
                  'PBLH_15','M10_15','M100_15','alpha_15','sinX100_15','cosX100_15',
                  'beta_15','SHFX_15','VENT_15','RH_15','T2_15','dT_15','Rig_15',
                  'PBLH_18','M10_18','M100_18','alpha_18','sinX100_18','cosX100_18',
                  'beta_18','SHFX_18','VENT_18','RH_18','T2_18','dT_18', 'Rig_18',
                  'PBLH_21','M10_21','M100_21','alpha_21','sinX100_21','cosX100_21',
                  'beta_21','SHFX_21','VENT_21','RH_21','T2_21','dT_21', 'Rig_21',
                  'PBLH_24','M10_24','M100_24','alpha_24','sinX100_24','cosX100_24',
                  'beta_24','SHFX_24','VENT_24','RH_24','T2_24','dT_24', 'Rig_24']       
    
df_new.insert(0, 'WDAY', WD)
df_new.insert(1, 'sinJDAY', np.sin(2*np.pi*JD/365))
df_new.insert(2, 'cosJDAY', np.cos(2*np.pi*JD/365))

df_new['NO2'] = NO2

In [8]:
print(df_new)

       WDAY   sinJDAY   cosJDAY       PBLH_0     M10_0     M100_0   alpha_0  \
0         1  0.017213  0.999852   561.224548  4.889100   7.314023  0.174927   
1         1  0.017213  0.999852   728.104553  5.642797   9.618214  0.231600   
2         1  0.017213  0.999852   890.024536  3.335469   6.549621  0.293059   
3         1  0.017213  0.999852   831.464539  7.110527  10.220735  0.157580   
4         1  0.017213  0.999852  1074.344482  6.011021  10.840692  0.256109   
...     ...       ...       ...          ...       ...        ...       ...   
36126     5 -0.858764  0.512371   286.723053  3.180732   5.633201  0.248228   
36127     5 -0.858764  0.512371   266.403046  3.256335   5.965627  0.262927   
36128     5 -0.858764  0.512371   119.763054  2.841368   4.975722  0.243329   
36129     5 -0.858764  0.512371   266.403046  3.256335   5.965627  0.262927   
36130     5 -0.858764  0.512371   119.763054  2.841368   4.975722  0.243329   

       sinX100_0  cosX100_0    beta_0  ...  sinX100

#### Save dataframe to a csv file

In [9]:
df_new.to_csv(EXTDATA_DIR + 'train/GFS/' + 'trainGFS.csv', index=False)